In [30]:
from rdkit import Chem
from rdkit.Chem import AllChem
import numpy as np

smiles = 'O=C(O)c1ccc(C(O)=O)cc1'
# Convert SMILES to a molecule object
mol = Chem.MolFromSmiles(smiles)
# Add hydrogen atoms to the molecule (Возможно лишнее)
mol = Chem.AddHs(mol)
# Generate 3D coordinates
AllChem.EmbedMolecule(mol, AllChem.ETKDG())

# Optimize the geometry (потенциально тоже опционально)
AllChem.UFFOptimizeMolecule(mol)

# Calculate the maximum distance between any two atoms
coords = mol.GetConformer().GetPositions()

max_length = np.max([np.linalg.norm(coords[i]-coords[j]) for i in range(len(coords)) for j in range(i+1, len(coords))])
max_length



9.206369901702057

In [32]:
mol_file_path = 'molecule.mol' 
# Сохранение в .mol файл для проверки
with open(mol_file_path, 'w') as writer: 
    writer.write(Chem.MolToMolBlock(mol))

In [1]:
from pymatgen.core.structure import Structure
from pymatgen.analysis.local_env import CrystalNN 
from pymatgen.analysis.graphs import StructureGraph
import networkx as nx
import numpy as np
import os
import pandas as pd


In [2]:
def analyze_mof(cif_file):
    # Load the MOF structure from the CIF file    
    structure = Structure.from_file(cif_file)
    # Initialize CrystalNN to find nearest neighbors
    cnn = CrystalNN(weighted_cn=True)    
    # Create a StructureGraph with local environment strategy
    structure_graph = StructureGraph.with_local_env_strategy(structure, cnn,weights=True)
    # Analyze and print structure graph
    # print("Analyzing structure graph:")
    # for i, site in enumerate(structure_graph.structure):
    #     print(f"Site {i}: {site.specie}, Coordination number: {len(structure_graph.get_connected_sites(i))}")

    # Analyze and print coordination numbers and types for each metal site    
    print("Analyzing coordination environments:")
    for i, site in enumerate(structure):        
        if site.specie.is_metal:
            cn = cnn.get_cn(structure, i, use_weights=True)            
            print(f"Metal {site.specie} at site {i}: Coordination number: {cn}")
            # Getting detailed coordination environment
            neighbors = cnn.get_nn_info(structure, i)            
            for neighbor in neighbors:
                print(f" - Neighbor: {neighbor['site'].species_string}, Distance: {neighbor['weight']:.3f}")
    

In [2]:
class MOFAnalyzer:
    def __init__(self, cif_file, threshold=0.01):
        self.cif_file = cif_file
        self.structure = Structure.from_file(cif_file)
        self.cnn = CrystalNN(weighted_cn=True)
        self.structure_graph = StructureGraph.with_local_env_strategy(self.structure, self.cnn, weights=True)
        self.threshold = threshold

    def analyze(self, threshold_distance = None):
        print("Analyzing coordination environments and their immediate environments:")
        for i, site in enumerate(self.structure):
            if site.specie.is_metal:
                self.analyze_metal_site(i, threshold_distance = threshold_distance)

    def analyze_metal_site(self, site_index, threshold_distance = None):
        if threshold_distance is None:
            threshold_distance = self.threshold

        site = self.structure[site_index]
        cn = self.cnn.get_cn(self.structure, site_index, use_weights=True)
        print(f"Metal {site.specie}({site_index}): Coordination number: {cn}")

        neighbors_info = self.cnn.get_nn_info(self.structure, site_index)
        filtered_neighbors_info = [info for info in neighbors_info if info['weight'] > threshold_distance]
        
        for info in filtered_neighbors_info:
            neighbor_site = info['site']
            print(f" - Neighbor: {neighbor_site.species_string}, Distance: {info['weight']:.3f}")

    def remove_edges_under_threshold(self, threshold_distance = None):
        if threshold_distance is None:
            threshold_distance = self.threshold

        new_edges = []
        for edge in self.structure_graph.graph.edges(data=True):
            # edge is a tuple like (u, v, data), where data contains edge attributes
            u, v, data = edge
            if 'weight' in data and data['weight'] >= threshold_distance:
                new_edges.append((u, v, data))
            elif 'weight' not in data:  # If no weight, use distance calculation as a fallback
                site_u = self.structure[u]
                site_v = self.structure[v]
                distance = site_u.distance(site_v)
                if distance >= threshold_distance:
                    new_edges.append((u, v, data))

        # Rebuild the graph with filtered edges
        self.structure_graph.graph.clear_edges()
        self.structure_graph.graph.add_edges_from(new_edges)
    
    def analyze_metal_neighbors_connections(self):
        nx_graph = self.structure_graph.graph.to_undirected()
        metal_site_indices = [i for i, site in enumerate(self.structure) if site.specie.is_metal]
        overall_connection_info = {}

        for metal_site_index in metal_site_indices:
            connection_info = {}
            metal_neighbors = [nbr for nbr in nx_graph.neighbors(metal_site_index)]
            non_metal_neighbors = [nbr for nbr in metal_neighbors if not self.structure[nbr].specie.is_metal]

            # Analyze direct connections to non-metal neighbors
            # for neighbor_index in non_metal_neighbors:
            #     formatted_neighbor = self.format_atom_info(neighbor_index)
            #     connection_info[formatted_neighbor] = {'connected': True, 'path': []}

            # Analyze connections between metal and non-metal neighbors, avoiding duplicates
            analyzed_pairs = set()
            for i, neighbor_1 in enumerate(non_metal_neighbors):
                for neighbor_2 in non_metal_neighbors[i + 1:]:
                    if (neighbor_1, neighbor_2) not in analyzed_pairs:
                        try:
                            non_metal_subgraph = nx_graph.subgraph([n for n in nx_graph.nodes if not self.structure[n].specie.is_metal])
                            path = nx.shortest_path(non_metal_subgraph, source=neighbor_1, target=neighbor_2)
                            formatted_path = [self.format_atom_info(n) for n in path]
                            connection_info[(self.format_atom_info(neighbor_1), self.format_atom_info(neighbor_2))] = {'connected': True, 'path': formatted_path}
                            analyzed_pairs.add((neighbor_1, neighbor_2))
                        except nx.NetworkXNoPath:
                            connection_info[(self.format_atom_info(neighbor_1), self.format_atom_info(neighbor_2))] = {'connected': False}

            # Find all paths between metal atoms through non-metal intermediates
            for neighbor_index in metal_neighbors:
                if self.structure[neighbor_index].specie.is_metal and neighbor_index != metal_site_index:
                    all_paths = self.find_all_paths(nx_graph, metal_site_index, neighbor_index, path=[])
                    if all_paths:
                        for path_index, path in enumerate(all_paths, start=1):
                            # Exclude direct metal-metal paths
                            if len(path) > 2 and all(not self.structure[node].specie.is_metal for node in path[1:-1]):
                                formatted_path = [self.format_atom_info(n) for n in path]
                                connection_info[(self.format_atom_info(metal_site_index), self.format_atom_info(neighbor_index), path_index)] = {'connected': True, 'path': formatted_path}
                    else:
                        connection_info[(self.format_atom_info(metal_site_index), self.format_atom_info(neighbor_index))] = {'connected': False}

            overall_connection_info[self.format_atom_info(metal_site_index)] = connection_info

        return overall_connection_info
    
    def format_atom_info(self, site_index):
        """
        Returns a formatted string with the species and site index of an atom.
        """
        site = self.structure[site_index]
        return f"{site.specie}({site_index})"
    
    def find_all_paths(self, graph, start_node, end_node, path=[], max_length=5):
        """
        Recursively finds all paths from start_node to end_node in graph, with path length not exceeding max_length.
        """
        path = path + [start_node]
        
        # Stop and return empty list if the path length exceeds the maximum allowed length
        if len(path) > max_length:
            return []
        
        if start_node == end_node:
            return [path]
        if start_node not in graph:
            return []
        
        paths = []
        for node in graph.neighbors(start_node):
            if node not in path:
                newpaths = self.find_all_paths(graph, node, end_node, path, max_length)
                for newpath in newpaths:
                    paths.append(newpath)
        return paths
    
    def summarize_bonding_information(self):
       
        neighbors = {}  # Track all neighbors for metals atoms
        metal_link = {} # Track metal-metal pairs

        for metal, connections in self.analyze_metal_neighbors_connections().items():


            neighbors[metal] = {} # Track all neighbors for this metal atom
            
            # Analyze each connection with metals
            for pair, info in connections.items():
                if len(pair) == 3: # If the pair is a metal-metal path
                    atom1, atom2, _ = pair[0], pair[1], pair[2]
                    # TODO: collect unique metal-metal paths
                    fp = frozenset((atom1, atom2))
                    
                    # check if the pair is already in metal_link add if not
                    if fp not in metal_link.keys():
                        metal_link[fp] = {'path': [info['path']], 'bonding': 'scissors'}
                    # check if the path is already in metal_link add if not
                    elif all(set(info['path']) != set(path) for path in metal_link[fp]['path']):
                        metal_link[fp]['path'].append(info['path'])
                        

                else:
                    atom1, atom2 = pair[0], pair[1]
                    # If the pair non-metal-non-metal path exists and less than 8, add it to neighbors
                    if info['connected'] and len(info['path']) < 8:
                        neighbors[metal][atom1] = {'path': info['path'], 'bonding': 'double'}
                        neighbors[metal][atom2] = {'path': info['path'], 'bonding': 'double'}
                    # if neighbors[metal][atom1]['path'] or neighbors[metal][atom2]['path'] keys is not exist then create it
                    elif atom1 not in neighbors[metal]:
                        neighbors[metal][atom1] = {'path': None, 'bonding': 'hinge'}
                    elif atom2 not in neighbors[metal]:
                        neighbors[metal][atom2] = {'path': None, 'bonding': 'hinge'}    

                    # If the pair non-metal-non-metal path exists and more than 8, do not change information about bonding
                    elif neighbors[metal][atom1]['path'] is not None or neighbors[metal][atom2]['path'] is not None:
                        continue
                    # If the pair non-metal-non-metal path does not exist, set None to neighbors even if it already None
                    else:
                        neighbors[metal][atom1] = {'path': None, 'bonding': 'hinge'}
                        neighbors[metal][atom2] = {'path': None, 'bonding': 'hinge'}

        return neighbors, metal_link
    
    def final_bonding_info(self):

        neighbors, metal_link = self.summarize_bonding_information()
        final_info = []
        # Last check
        # If metal link is not empty ,we should take atoms from all path and check if they are neighbors of metals 
        # if they are neighbors of metals then we should change bonding type to scissors
        for k, v in metal_link.items():
            for path in v['path']:
                for atom in path:
                    for metal, conn in neighbors.items():
                        if atom in conn.keys():
                            conn[atom]['bonding'] = 'scissors'
                            conn[atom]['path'] = path
        
        # Final summary
        num_metal_atoms = len(neighbors)
        metal = list(neighbors.keys())[0]
        # Initialize counters and sets for the overall summary
        total_hinge_bond_atoms = set()
        total_double_bond_descriptions = set()
        total_scissors_bond_descriptions = set()
        total_num_hinge = 0
        total_num_double = 0
        total_num_scissors = 0

        # Process each metal atom's connections
        for metal, conn in neighbors.items():
            # Update counters and sets with information from this metal atom
            total_num_hinge += sum(1 for v in conn.values() if v['bonding'] == 'hinge')
            total_num_double += sum(1 for v in conn.values() if v['bonding'] == 'double') / 2  # Adjust for double counting
            total_num_scissors += sum(1 for v in conn.values() if v['bonding'] == 'scissors')
            
            total_hinge_bond_atoms.update(k.split('(')[0] for k, v in conn.items() if v['bonding'] == 'hinge')
            total_double_bond_descriptions.update(set('-'.join(v['path']) for k, v in conn.items() if v['bonding'] == 'double' and v['path'] is not None))
            total_scissors_bond_descriptions.update(set('-'.join(v['path']) for k, v in conn.items() if v['bonding'] == 'scissors' and v['path'] is not None))

        # Summarize the information for all metal atoms
        final_info.append({
            'cif file': self.cif_file.split(os.path.sep)[-1].split('.')[0],
            'metal atom' : metal.split('(')[0],
            'total num of metal atoms': num_metal_atoms,
            'total num of hinge bonding': total_num_hinge,
            'atoms in hinge bonding': ', '.join(total_hinge_bond_atoms) or 'None',
            'total num of double bonding': total_num_double,
            'atoms in double bonding': ', '.join(total_double_bond_descriptions) or 'None',
            'total num of scissors bonding': total_num_scissors,
            'atoms in scissors bonding': ', '.join(total_scissors_bond_descriptions) or 'None',
        })

        return final_info




In [114]:
a = ('a','b')
b = ('b','с')
# how to check that a and b have the same elements

fa = frozenset(a)
fb = frozenset(b)
c = {}

c[fa]= {'pair': set(a), 'path': [[1,2,3],[1,3,2]], 'bonding': 'scissors'}
c[fb]= {'pair': set(b), 'path': [[2,4,3],[1,5,6]], 'bonding': 'scissors'}

d = [1,6,5]
print(all(set(d) != set(i) for i in c[fb]['path']))
len(c)
# if set(b) not in c:
#     c[b] = {'pair': set(b), 'path': [1,2,3], 'bonding': 'scissors'}
# print(c)

False


2

In [5]:
path = 'test_cifs'

In [8]:
analyzer = MOFAnalyzer(os.path.join(path,'qmof-1a36e21.cif'), threshold=0.1)

analyzer.remove_edges_under_threshold()
# analyzer.analyze()
# analyzer.structure_graph.draw_graph_to_file('graph_filt_qmof.png', node_labels='atom',hide_image_edges=False)
# coonnections = analyzer.analyze_metal_neighbors_connections()
# print(coonnections)
summary = analyzer.final_bonding_info()
print(summary)



FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\v.shirobokov\\Documents\\git repo\\PPTiM\\relaxed_structures\\qmof-1a36e21.cif'

In [3]:
# open all csv and unite them
path = 'C:\\Users\\v.shirobokov\\Documents\\git repo\\PPTiM\\knn data'
df = pd.DataFrame()
for file in os.listdir(path):
    if file.endswith(".csv"):
        data = pd.read_csv(os.path.join(path, file))
        df = pd.concat([df, data], ignore_index=True)


import json
with open('C:\\Users\\v.shirobokov\\Documents\\git repo\\PPTiM\\preprocessing\\qmof\\map_names.json', 'r') as f:
    dict_names = json.load(f)


# Переворачиваем словарь для поиска по значениям
dict_flipped = {v: k for k, v in dict_names.items()}

# Используем apply для применения функции к каждому элементу столбца 'col 1'
# Функция возвращает ключ из перевернутого словаря, если значение найдено, иначе None
keys_in_df = df[df.columns[0]].apply(lambda x: dict_flipped.get(x, None))

# Фильтруем None значения, чтобы получить только совпадения
keys_in_df = keys_in_df.dropna()
keys_in_list = keys_in_df.tolist()

print(keys_in_list)
print(len(keys_in_list))

['qmof-1a36e21', 'qmof-9d35285', 'qmof-a328797', 'qmof-5e8c015', 'qmof-1c7dc6d', 'qmof-ef5f46f', 'qmof-8708a28', 'qmof-a7c79f1', 'qmof-683accb', 'qmof-87f9fa2', 'qmof-8bbce0c', 'qmof-fcdce3e', 'qmof-79de66a', 'qmof-e8a127b', 'qmof-7c567fa', 'qmof-22e67b2', 'qmof-fae0ae2', 'qmof-5e5ad16', 'qmof-316a890', 'qmof-d14fd27', 'qmof-312525c', 'qmof-3c63b34', 'qmof-2972f3b', 'qmof-e454c8c', 'qmof-ee0dc19', 'qmof-955fe88', 'qmof-8bfd99e', 'qmof-a680360', 'qmof-a268ce5', 'qmof-df89737', 'qmof-a6a203e', 'qmof-d77d3f0', 'qmof-19da9fb', 'qmof-fc04194', 'qmof-3ab81f0', 'qmof-e0a081e', 'qmof-19a8d62', 'qmof-e2faba1', 'qmof-7aebbbb', 'qmof-e019673', 'qmof-a377fcc', 'qmof-235f291', 'qmof-e726ffa', 'qmof-90ea100', 'qmof-1b7741c', 'qmof-57e97e1', 'qmof-0b8fec1', 'qmof-e3a50a7', 'qmof-dd5a73e', 'qmof-b405c94', 'qmof-a6e0d05', 'qmof-0e64acd', 'qmof-d943a25', 'qmof-c65a3b9', 'qmof-fe4cda4', 'qmof-5a1b96a', 'qmof-7770304', 'qmof-37ec311', 'qmof-a2b803b', 'qmof-f85760f', 'qmof-238a7a1', 'qmof-0d451dd', 'qmof-7

In [4]:
path = 'C:\\Users\\v.shirobokov\\Documents\\git repo\\PPTiM\\relaxed_structures\\relaxed_structures'

summary_df = pd.DataFrame()
# for file in os.listdir(path):
for file in keys_in_list:
    print(file)
    file_name = file + '.cif'
    try:
        analyzer = MOFAnalyzer(os.path.join(path,file_name), threshold=0.1)
        analyzer.remove_edges_under_threshold()
        # analyzer.analyze()
        # analyzer.structure_graph.draw_graph_to_file(f'graph_{file}.png', node_labels='atom', hide_image_edges=False)
        # connections= analyzer.analyze_metal_neighbors_connections()
        # print(connections)
        summary = analyzer.final_bonding_info()
        df = pd.DataFrame(summary)
        summary_df = pd.concat([summary_df, df], ignore_index=True)
        # print(summary)
        print("_______________________________________________")
    
    except Exception as e:
        print(f'Error with {file}', e)
        continue

summary_df.to_csv('summary_tr01.csv', index=False)

qmof-1a36e21


c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:4135: UserWarning: No oxidation states specified on sites! For better results, set the site oxidation states in the structure.
  warnings.warn(
c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:3928: UserWarning: CrystalNN: cannot locate an appropriate radius, covalent or atomic radii will be used, this can lead to non-optimal results.
  warnings.warn(


_______________________________________________
qmof-9d35285


c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:4135: UserWarning: No oxidation states specified on sites! For better results, set the site oxidation states in the structure.
  warnings.warn(
c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:3928: UserWarning: CrystalNN: cannot locate an appropriate radius, covalent or atomic radii will be used, this can lead to non-optimal results.
  warnings.warn(


_______________________________________________
qmof-a328797


...

_______________________________________________
qmof-25172f2


c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:4135: UserWarning: No oxidation states specified on sites! For better results, set the site oxidation states in the structure.
  warnings.warn(
c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:3928: UserWarning: CrystalNN: cannot locate an appropriate radius, covalent or atomic radii will be used, this can lead to non-optimal results.
  warnings.warn(


_______________________________________________
qmof-66998fd


c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:4135: UserWarning: No oxidation states specified on sites! For better results, set the site oxidation states in the structure.
  warnings.warn(
c:\Users\v.shirobokov\AppData\Local\anaconda3\envs\pptim\lib\site-packages\pymatgen\analysis\local_env.py:3928: UserWarning: CrystalNN: cannot locate an appropriate radius, covalent or atomic radii will be used, this can lead to non-optimal results.
  warnings.warn(


_______________________________________________
